In [8]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np

def plot_score_distributions(df, score_cols, bottom_percentile=0, top_percentile=100):
    """
    Plots distributions for each analytic score column, with optional exclusion of bottom/top percentiles, using Plotly.
    For *_SIGNED_DIST columns, increase x-tick frequency for readability.
    """
    signed_dist_cols = [c for c in score_cols if c.endswith('_SIGNED_DIST')]
    df_scores = df[score_cols].copy()
    # Remove bottom/top percentiles if specified
    if bottom_percentile > 0 or top_percentile < 100:
        for col in score_cols:
            low = np.percentile(df_scores[col], bottom_percentile)
            high = np.percentile(df_scores[col], top_percentile)
            df_scores = df_scores[(df_scores[col] >= low) & (df_scores[col] <= high)]
    num_cols = len(score_cols)
    nrows = (num_cols + 1) // 2
    fig = make_subplots(rows=nrows, cols=2, subplot_titles=score_cols)
    for i, col in enumerate(score_cols):
        row = i // 2 + 1
        col_num = i % 2 + 1
        hist = go.Histogram(x=df_scores[col], nbinsx=30, name=col, histnorm='probability density', opacity=0.75)
        fig.add_trace(hist, row=row, col=col_num)
        if col in signed_dist_cols:
            ticks = np.linspace(df_scores[col].min(), df_scores[col].max(), 15)
            fig.update_xaxes(tickvals=ticks, row=row, col=col_num)
    fig.update_layout(height=300*nrows, width=900, showlegend=False, title_text='Distribution of Analytic Scores')
    fig.show()

# Load the data
scores_path = '../data/processed_data/merged_analytic_scores.csv'
df = pd.read_csv(scores_path)
# Get all columns after 'activity_cluster_label'
start_col = df.columns.get_loc('activity_cluster_label') + 1
score_cols = df.columns[start_col:]

# Example usage: exclude bottom 1% and top 99%
from plotly.subplots import make_subplots
plot_score_distributions(df, score_cols, bottom_percentile=2.5, top_percentile=97.5)
# To plot all data, use: plot_score_distributions(df, score_cols)

BELOW IS LOOKING AT THE POSSIBLE "STABLE HIGH-VALUE TRADER" POTENTIAL BEHAVIOURAL ARCHETYPE

In [15]:
# Identify 'stable high-value traders' and compare to rest (Plotly version)
import numpy as np
import plotly.graph_objects as go

# Function to plot two distributions for a given column
def plot_group_comparison(data1, data2, col, label1, label2, title, xlabel=None, bottom_percentile=0, top_percentile=100, stat='density'):
    """
    Plots two distributions for a given column, with optional exclusion of bottom/top percentiles, using Plotly.
    """
    d1 = data1[col]
    d2 = data2[col]
    if bottom_percentile > 0 or top_percentile < 100:
        low1 = np.percentile(d1, bottom_percentile)
        high1 = np.percentile(d1, top_percentile)
        d1 = d1[(d1 >= low1) & (d1 <= high1)]
        low2 = np.percentile(d2, bottom_percentile)
        high2 = np.percentile(d2, top_percentile)
        d2 = d2[(d2 >= low2) & (d2 <= high2)]
    fig = go.Figure()
    fig.add_trace(go.Histogram(x=d1, name=label1, nbinsx=30, histnorm='probability density' if stat=='density' else '', marker_color='blue', opacity=0.75))
    fig.add_trace(go.Histogram(x=d2, name=label2, nbinsx=30, histnorm='probability density' if stat=='density' else '', marker_color='grey', opacity=0.5))
    fig.update_layout(barmode='overlay', title=title, xaxis_title=(xlabel if xlabel else col), yaxis_title=('Density' if stat=='density' else 'Count'))
    fig.show()

# Define score columns
vol_col = 'BEHAVIOURAL_VOLATILITY_SCORE'
rev_col = 'REVENUE_SCORE_PROXY'
cross_col = 'CROSS_DOMAIN_ENGAGEMENT_SCORE'
im_dist_cols = [col for col in df.columns if col.endswith('_NORM_DIST')]

# Set volatility threshold to 0.5
vol_thresh = 0.5
# Set revenue threshold to 5000 (instead of 75th percentile)
rev_thresh = 3000

# Select group: volatility < 0.5, high revenue
stable_high_value = df[(df[vol_col] < vol_thresh) & (df[rev_col] > rev_thresh)]
rest = df[~((df[vol_col] < vol_thresh) & (df[rev_col] > rev_thresh))]

print(f"Stable high-value traders: {len(stable_high_value)} wallets ({len(stable_high_value)/len(df)*100:.1f}% of total)")

# Example: Remove top and bottom 5% outliers for all plots
bottom_percentile = 5
top_percentile = 95

# 1. Distribution of volatility (comparison)
plot_group_comparison(stable_high_value, rest, vol_col, 'Stable High-Value', 'Rest', 'Behavioural Volatility Score', bottom_percentile=bottom_percentile, top_percentile=top_percentile)

# 2. Distribution of revenue (comparison) - use density on y-axis
plot_group_comparison(stable_high_value, rest, rev_col, 'Stable High-Value', 'Rest', 'Revenue Proxy Score', xlabel='Revenue Proxy Score (outliers removed)', bottom_percentile=bottom_percentile, top_percentile=top_percentile, stat='density')

# 3. Cross Domain Engagement Score: compare group to whole dataset
plot_group_comparison(stable_high_value, df, cross_col, 'Stable High-Value', 'All Wallets', 'Cross Domain Engagement Score (Stable High-Value vs All Wallets)', xlabel='Cross Domain Engagement Score', bottom_percentile=bottom_percentile, top_percentile=top_percentile)

# 4. Interaction Mode Distance Scores: compare group vs rest
for col in im_dist_cols:
    plot_group_comparison(stable_high_value, rest, col, 'Stable High-Value', 'Rest', f'{col} (Stable High-Value vs Rest)', bottom_percentile=bottom_percentile, top_percentile=top_percentile)


Stable high-value traders: 528 wallets (2.6% of total)


THE BELOW IS LOOKING AT THE POTENTIAL "ERRATIC SPECULATOR" BEHAVIOURAL ARCHETYPE

In [10]:
# Compare wallets with high volatility (>0.6) and low cross-domain engagement (<0.25) to the rest, and visualise their cluster distribution and all other analytic scores (Plotly version)
import plotly.graph_objects as go
import numpy as np

# Define analytic score columns (update if your column names differ)
vol_col = 'BEHAVIOURAL_VOLATILITY_SCORE'
cross_col = 'CROSS_DOMAIN_ENGAGEMENT_SCORE'
cluster_col = 'activity_cluster_label'
# Use score_cols from previous cells if available, else define manually if needed
# score_cols = [vol_col, cross_col, ...]
# If not defined, get all columns after 'activity_cluster_label'
if 'score_cols' not in locals():
    start_col = df.columns.get_loc(cluster_col) + 1
    score_cols = df.columns[start_col:]

# Select wallets with the specified limitations
limited = df[(df[vol_col] > 0.6) & (df[cross_col] < 0.25)]
rest = df[~((df[vol_col] > 0.6) & (df[cross_col] < 0.25))]

print(f"Wallets with {vol_col} > 0.6 and {cross_col} < 0.25: {len(limited)} ({len(limited)/len(df)*100:.2f}% of total)")

# 1. Visualise the distribution of all analytic scores for both groups (Plotly)
num_cols = len(score_cols)
nrows = (num_cols + 1) // 2
from plotly.subplots import make_subplots
fig = make_subplots(rows=nrows, cols=2, subplot_titles=score_cols)
for i, col in enumerate(score_cols):
    row = i // 2 + 1
    col_num = i % 2 + 1
    fig.add_trace(go.Histogram(x=limited[col], name='Limited', nbinsx=30, histnorm='probability density', marker_color='red', opacity=0.75), row=row, col=col_num)
    fig.add_trace(go.Histogram(x=rest[col], name='Rest', nbinsx=30, histnorm='probability density', marker_color='grey', opacity=0.5), row=row, col=col_num)
    fig.update_xaxes(title_text=col, row=row, col=col_num)
    fig.update_yaxes(title_text='Density', row=row, col=col_num)
    if i == 0:
        fig.update_layout(showlegend=True)
    # Improve x-tick frequency for *_SIGNED_DIST columns
    if col.endswith('_SIGNED_DIST'):
        ticks = np.linspace(min(limited[col].min(), rest[col].min()), max(limited[col].max(), rest[col].max()), 15)
        fig.update_xaxes(tickvals=ticks, row=row, col=col_num)
fig.update_layout(height=300*nrows, width=900, title_text='Distribution of Analytic Scores: Limited vs Rest', barmode='overlay')
fig.show()

# 2. Visualise which clusters the limited wallets are in, compared to the rest (Plotly)
import plotly.express as px
cluster_order = sorted(df[cluster_col].unique())
all_wallets_counts = limited[cluster_col].value_counts().reindex(cluster_order, fill_value=0)
rest_counts = rest[cluster_col].value_counts().reindex(cluster_order, fill_value=0)
df_bar = pd.DataFrame({'Cluster': cluster_order, 'Limited': all_wallets_counts.values, 'Rest': rest_counts.values})
fig2 = go.Figure()
fig2.add_trace(go.Bar(x=df_bar['Cluster'], y=df_bar['Rest'], name='Rest', marker_color='grey', opacity=0.5))
fig2.add_trace(go.Bar(x=df_bar['Cluster'], y=df_bar['Limited'], name='Limited', marker_color='red', opacity=0.8))
fig2.update_layout(barmode='overlay', title='Cluster Distribution: Limited vs All Wallets', xaxis_title='Cluster Label', yaxis_title='Count')
fig2.show()

Wallets with BEHAVIOURAL_VOLATILITY_SCORE > 0.6 and CROSS_DOMAIN_ENGAGEMENT_SCORE < 0.25: 6079 (30.13% of total)


Exploring the potential behavioural archetypes of wallets that are seen in the analytic scores - "DEFI POWER USER"

In [11]:
# Compare wallets with DEFI_EVENTS_SIGNED_DIST < 11 to the rest, and visualise all analytic scores and cluster distribution, with optional outlier removal (Plotly version)
import plotly.graph_objects as go
import numpy as np
import pandas as pd
from plotly.subplots import make_subplots

# Define the relevant column
defi_dist_col = 'DEFI_EVENTS_SIGNED_DIST'
cluster_col = 'activity_cluster_label'
# Use score_cols from previous cells if available, else define manually if needed
if 'score_cols' not in locals():
    start_col = df.columns.get_loc(cluster_col) + 1
    score_cols = df.columns[start_col:]

# Set percentiles for outlier removal (set to 0 and 100 for no trimming)
bottom_percentile = 10
top_percentile = 100

# Select wallets with the specified limitation
limited = df[df[defi_dist_col] < 11]
rest = df[~(df[defi_dist_col] < 11)]

print(f"Wallets with {defi_dist_col} < 11: {len(limited)} ({len(limited)/len(df)*100:.2f}% of total)")

# 1. Visualise the distribution of all analytic scores for both groups, with optional outlier removal (Plotly)
num_cols = len(score_cols)
nrows = (num_cols + 1) // 2
fig = make_subplots(rows=nrows, cols=2, subplot_titles=score_cols)
for i, col in enumerate(score_cols):
    # Remove outliers using percentiles if specified
    lim_low, lim_high = np.percentile(limited[col], bottom_percentile), np.percentile(limited[col], top_percentile)
    rest_low, rest_high = np.percentile(rest[col], bottom_percentile), np.percentile(rest[col], top_percentile)
    limited_trimmed = limited[(limited[col] >= lim_low) & (limited[col] <= lim_high)][col]
    rest_trimmed = rest[(rest[col] >= rest_low) & (rest[col] <= rest_high)][col]
    row = i // 2 + 1
    col_num = i % 2 + 1
    fig.add_trace(go.Histogram(x=limited_trimmed, name='Limited', nbinsx=30, histnorm='probability density', marker_color='red', opacity=0.75), row=row, col=col_num)
    fig.add_trace(go.Histogram(x=rest_trimmed, name='Rest', nbinsx=30, histnorm='probability density', marker_color='grey', opacity=0.5), row=row, col=col_num)
    fig.update_xaxes(title_text=col, row=row, col=col_num)
    fig.update_yaxes(title_text='Density', row=row, col=col_num)
    if i == 0:
        fig.update_layout(showlegend=True)
    # Improve x-tick frequency for *_SIGNED_DIST columns
    if col.endswith('_SIGNED_DIST'):
        ticks = np.linspace(min(limited_trimmed.min(), rest_trimmed.min()), max(limited_trimmed.max(), rest_trimmed.max()), 15)
        fig.update_xaxes(tickvals=ticks, row=row, col=col_num)
fig.update_layout(height=300*nrows, width=900, title_text='Distribution of Analytic Scores: Limited (DEFI_EVENTS_SIGNED_DIST < 11) vs Rest', barmode='overlay')
fig.show()

# 2. Visualise which clusters the limited wallets are in, compared to the rest (Plotly)
cluster_order = sorted(df[cluster_col].unique())
all_wallets_counts = limited[cluster_col].value_counts().reindex(cluster_order, fill_value=0)
rest_counts = rest[cluster_col].value_counts().reindex(cluster_order, fill_value=0)
df_bar = pd.DataFrame({'Cluster': cluster_order, 'Limited': all_wallets_counts.values, 'Rest': rest_counts.values})
fig2 = go.Figure()
fig2.add_trace(go.Bar(x=df_bar['Cluster'], y=df_bar['Rest'], name='Rest', marker_color='grey', opacity=0.5))
fig2.add_trace(go.Bar(x=df_bar['Cluster'], y=df_bar['Limited'], name='Limited', marker_color='red', opacity=0.8))
fig2.update_layout(barmode='overlay', title='Cluster Distribution: Limited (DEFI_EVENTS_SIGNED_DIST < 11) vs All Wallets', xaxis_title='Cluster Label', yaxis_title='Count')
fig2.show()

KeyError: 'DEFI_EVENTS_SIGNED_DIST'